# Modèles et Algorithmes des Réseaux
## TD du 6 novembre 2018

In [ ]:
import numpy as np
import random
import math
import heapq as hq

import networkx as nx
%matplotlib notebook
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D

## Trafic HTTP

On modélise le trafic HTTP d'un site web comme suit :

- Le trafic est composé de _sessions_, qui débutent selon un processus ponctuel de Poisson d'intensité $\lambda$ ;
- Chaque session comporte un certain nombre de _clicks_, distribué géométriquement avec paramètre $\rho$ ;
- Chaque click génère une certaine _charge_ (nombre de paquets), qui suit une loi Zêta de paramètre $\gamma$ : $$\mathbf P(C = k) = Z k^{-\gamma} \ ;$$
- La durée entre deux clicks d'une même session suit une loi de Weibull de paramètres $\mu$ et $\nu$ : $$\mathbf P(I > x) = e^{-\mu x^{\nu}}.$$

Implémenter le schéma de Matthes permettant de calculer la charge totale $A(t)$ reçue dans l'intervalle de temps $[0;t]$.

In [ ]:
def http(l, r, g, m, n, T):
    raise NotImplementedError

In [ ]:
def plot_http(jumps):
    ax = plt.figure().gca()
    
    ax.step([j[0] for j in jumps], [j[1] for j in jumps], where='post')

    plt.show(block=False)

In [ ]:
plot_http(http(.2, .1, 3, 1, 2, 1000))
#plot_http(http(.01, .9, 3, 1, 2, 1000))

## Échantillonage préférentiel

On considère la réserve d'une assurance. En temps normal, celle-ci augmente linéairement avec le temps. Il lui arrive cependant de subir des chutes brutales. On modélise l'évolution ainsi :

- La réserve initiale est $X_0$ ;
- L'augmentation est de $a$ par unité de temps ;
- Les chutes se produisent selon un processus ponctuel de Poisson de paramètre $\lambda$ ;
- Lors d'une chute, la perte $Y$ suit une loi de Pareto d'amplitude $m$ et de forme $k$.

On veut déterminer la probabilité de faire faillite avant l'horizon $T$.

1. Écrire une fonction `simul(X0, a, l, m, k, T)` qui modélise l'évolution du système jusqu'à l'instant $T$, et renvoit le couple `(survie, chutes)`, où `survie` est un booléen et `chutes` le nombre de chutes lors de la simulation.
1. En prenant pour paramètres $X_0=1$, $a=1$, $\lambda=0.001$, $m=10$, $k=1.5$ et $T=100$, examiner le nombre de faillites sur $I = 10000$ itérations.
1. On remarque que
$$\mathbf P_\lambda({\rm ruine})
= \sum_S \mathbf 1_{\rm ruine}(S) \mathbf P_\lambda(S)
= \sum_S \mathbf 1_{\rm ruine}(S) \frac{\mathbf P_\lambda(S)}{\mathbf P_\mu(S)} \mathbf P_\mu(S)
\approx \frac1n \sum_{i=0}^n \mathbf 1_{\rm ruine}(S_i) \frac{\mathbf P_\lambda(S_i)}{\mathbf P_\mu(S_i)},$$
les séquences $S_i$ ayant été calculées avec $\mu$ comme paramètre pour le processus ponctuel de Poisson.
<br />
En remplaçant $\lambda$ par $\mu$, où $\mu$ est choisi tel que $a - \mu \mathbf E[Y_0] = 0$, et en pondérant le résultat, il est donc possible de favoriser les événements rares lors de la simulation.
<br />
À vous de jouer : écrire une fonction `important(X0, a, l, m, k, T, I)` qui calcule la probabilité de faillite par échantillonage préférentiel.

In [ ]:
params = [1, 1, .001, 10, 1.5, 100]
I = 10000

In [ ]:
def simul(X0, a, l, m, k, T):
    raise NotImplementedError

print(sum([not simul(*params)[0] for i in range(I)]) / I)

In [ ]:
def important(X0, a, l, m, k, T, I):
    raise NotImplementedError

print(important(*params, I))

## Affichage d'un graphe sur un cercle

Le but de cet exercice est de tracer un graphe en plaçant ses sommets sur un cercle de sorte à minimiser la longueur totale des arêtes. La longueur d'une arête est ici définie comme la distance séparant les sommets le long du cercle (distance en sommets : 1 si adjacents, $\frac N2$ si à l'opposé, etc.).

On utilise une approche probabiliste en considérant une chaîne de Markov (inhomogène) $(X_t)$ sur l'ensemble des configurations. La configuration initiale est tirée au hasard. À chaque étape, on choisi deux sommets $v$ et $w$ indépendants et uniformément distribués. On les échange avec probabilité $p_t$, où

- $p_t=1$ si cela fait diminuer la longueur totale des arêtes ;
- $p_t=e^{-\frac{(\Lambda_t^+ - \Lambda_t^-)}{\eta_t}}$ sinon, où $\Lambda_t^+$ et $\Lambda_t^-$ sont les longueurs totales après et avant échange, et $\eta_t \approx \log^{-1}(t)$.

À vous de jouer. On pourra tester avec les différents graphes aléatoires proposés par `networkx` (Erdős-Rényi, $d$-régulier, Barasi-Albert, etc.).

In [ ]:
def ring(G, iterations=10000):
    raise NotImplementedError

In [ ]:
def draw_ring(G, permutation):
    ax = plt.figure().gca()
    
    ax.plot([math.cos(2 * math.pi * permutation[v] / len(G)) for v in G.nodes],
            [math.sin(2 * math.pi * permutation[v] / len(G)) for v in G.nodes],
            'ro')
    
    for e in G.edges:
        ax.plot([math.cos(2 * math.pi * permutation[v] / len(G)) for v in e],
                [math.sin(2 * math.pi * permutation[v] / len(G)) for v in e],
                'b')

    plt.show(block=False)

In [ ]:
G = nx.random_regular_graph(6, 40)
#G = nx.barabasi_albert_graph(40, 2)
#G = nx.gnm_random_graph(40, 120)

draw_ring(G, ring(G))

## Affichage d'un graphe en 3 dimensions

Une des méthodes les plus utilisées consiste à adopter une approche physique : on considère que les sommets portent tous une même charge (disons 1), et se repoussent donc, alors que les arêtes officient comme des ressorts de même longueur à vide (au hasard : 1). On ajoute par ailleurs un bruit gaussien à chaque itération.

On considère une chaîne de Markov dont l'état initial est quelconque : les positions des sommets i.i.d., uniformes sur $[0,1]^3$. À chaque itération, on modifie la position d'un unique sommet $v$, tiré uniformément.

Modélisation des forces :

- Comme dans l'exercice précédent, on a un facteur d'atténuation $\eta_t$ qui décroît en $\log^{-1}(t)$ ;
- Loi de Coulomb : chaque sommet $w \neq v$ repousse $v$ avec amplitude $\frac{\eta_t}{d(v,w)^2}$ ;
- Loi de Hooke (ressorts) : chaque voisin $w$ de $v$ attire $v$ avec amplitude $\eta_t (1 - d(v,w))$ ;
- Le bruit gaussien est centré, de variance $\eta_t$.

In [ ]:
def embed(G, iterations = 10000):
    raise NotImplementedError

In [ ]:
def draw3D(G, coords):
    ax = plt.figure().gca(projection='3d')

    ax.scatter(*[[coords[v][x] for v in G.nodes] for x in range(3)])
    for e in G.edges:
        ax.plot(*[[coords[v][x] for v in e] for x in range(3)])

    plt.show(block=False)

In [ ]:
G = nx.random_regular_graph(3, 60)
#G = nx.barabasi_albert_graph(40, 2)
#G = max(nx.connected_component_subgraphs(nx.gnm_random_graph(40, 120)), key=len)

draw3D(G, embed(G))